In [2]:
%load_ext autoreload
%autoreload 2
# add . to module name
import sys
sys.path.append('../src/')

In [3]:
from package.logger import Timed, rlog, setup
from package import storage
setup("INFO")

In [4]:
import os
import psutil
import time

import folium
import geopandas as gpd
import pandas as pd
from h3 import h3
from typing import List, Set

from package import strtime
from package.osm import osm
from package.mcr import mcr
from package.mcr.mcr import MCR
from package.mcr.data import MCRGeoData
from package.mcr5.h3 import (
    get_h3_cells_for_nodes,
    get_h3_cells_for_bbox,
    plot_h3_cells_on_folium,
)
from package.mcr5.h3_osm_interaction import get_location_mappings_for_cells
from package.mcr5.mcr5 import MCR5
from package.mcr5.osm import add_nearest_osm_node_id
from package.mcr5.labels import read_labels_for_nodes


In [5]:
city_id = "Koeln"
stops_path = "../data/cleaned/stops.csv"
osm_path = osm.get_osm_path_from_city_id(city_id)

with Timed.info("Reading stops"):
	other_stops_df = storage.read_gdf(stops_path)

if not os.path.exists(osm_path) and city_id:
	rlog.info("Downloading OSM data")
	osm.download_city(city_id, osm_path)
else:
	rlog.info("Using existing OSM data")

osm_reader = osm.new_osm_reader(osm_path)

with Timed.info("Getting OSM graph"):
	nodes, edges = osm.get_graph_for_city_cropped_to_stops(osm_reader, other_stops_df)

[16:06:18] INFO     Reading stops                                                                   ]8;id=807993;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=785740;file:///tmp/ipykernel_60688/1792129641.py#5\5]8;;\

           INFO     Reading stops done (0.13 seconds)                                               ]8;id=464882;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=820587;file:///tmp/ipykernel_60688/1792129641.py#5\5]8;;\

           INFO     Using existing OSM data                                                        ]8;id=723842;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=897606;file:///tmp/ipykernel_60688/1792129641.py#12\12]8;;\

           INFO     Getting OSM graph                                                              ]8;id=151259;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=310110;file:///tmp/ipykernel_60688/1792129641.py#16\16]8;;\

           INFO     Loading OSM network from cache                                                 ]8;id=355860;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=740633;file:///tmp/ipykernel_60688/1792129641.py#16\16]8;;\

[16:06:19] INFO     Getting OSM graph done (0.95 seconds)                                          ]8;id=909345;file:///tmp/ipykernel_60688/1792129641.py\1792129641.py]8;;\:]8;id=922697;file:///tmp/ipykernel_60688/1792129641.py#16\16]8;;\

In [6]:
nodes.head(3)

lon        lat                                               tags  \
0  6.932525  50.937519  {'TMC:cid_58:tabcd_1:Class': None, 'TMC:cid_58...   
1  6.932627  50.937519                                               None   
2  6.932735  50.937519  {'TMC:cid_58:tabcd_1:Class': None, 'TMC:cid_58...   

   timestamp  version  changeset          id                  geometry  
0          0        0          0    21063145  POINT (6.93252 50.93752)  
1          0        0          0  7151289920  POINT (6.93263 50.93752)  
2          0        0          0    10929975  POINT (6.93274 50.93752)

In [42]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)
m = folium.Map(location=[50.9333, 6.95], zoom_start=12)
plot_h3_cells_on_folium(h3_cells, m)
m

In [8]:
# Initialize Folium Map centered around Cologne, Germany
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)


# Get unique H3 cells covering the OSM nodes at a given resolution (e.g., 9)
resolution = 9

bbox_cologne_center = [50.92, 6.94, 50.96, 6.98]
h3_cells = get_h3_cells_for_bbox(*bbox_cologne_center, resolution=9)

# Plot H3 cells on the Folium map
plot_h3_cells_on_folium(h3_cells, m)

# draw bbox
folium.Rectangle(
	bounds=[[bbox_cologne_center[0], bbox_cologne_center[1]], [bbox_cologne_center[2], bbox_cologne_center[3]]],
	color='red',
	fill=False,
).add_to(m)

# Show the map
m

In [9]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)
# h3_cells = get_h3_cells_for_bbox(*bbox_cologne_center, resolution=9)

In [39]:
location_mappings, invalid_h3_cells = get_location_mappings_for_cells(list(h3_cells), nodes, 20)

In [40]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(invalid_h3_cells, m)
m

In [41]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(map(lambda lm: lm.h3_cell, location_mappings), m)
nodes_by_id = nodes.set_index("id")
for location_mapping in location_mappings:
	node = nodes_by_id.loc[location_mapping.osm_node_id]
	folium.CircleMarker(
		location=(node.lat, node.lon),
		icon=folium.Icon(color="green"),
		radius=1,
		color="red",
	).add_to(m)
m

In [29]:
stops = "../data/cleaned/stops.csv"
city_id = "Koeln"
structs = "../data/structs.pkl"

In [30]:
mcr_geo_data = MCRGeoData(
	stops, structs, city_id
)

[14:21:30] INFO     Reading stops                                                                        ]8;id=261243;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=57164;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#31\31]8;;\

           INFO     Reading stops done (0.04 seconds)                                                    ]8;id=602288;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=264181;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#31\31]8;;\

           INFO     Preparing graphs                                                                     ]8;id=703089;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=344224;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Using existing OSM data                                                              ]8;id=433423;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=582636;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Loading OSM network from cache                                                       ]8;id=426632;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=971747;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

[14:21:47] INFO     Preparing graphs done (17.71 seconds)                                                ]8;id=171337;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=836330;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Creating graph cache                                                                 ]8;id=917974;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=933346;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#96\96]8;;\

[14:21:52] INFO     Creating graph cache done (4.23 seconds)                                             ]8;id=449241;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=100555;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#96\96]8;;\

In [32]:
mcr5 = MCR5(geo_data=mcr_geo_data, max_processes=12)

In [107]:
mcr5_output_path = "../data/mcr5/Koeln"

In [34]:
mcr5.run(location_mappings[:10], start_time="08:00:00", output_dir=mcr5_output_path)

All processes finished.                                         


In [36]:
import overpy

api = overpy.Overpass()

# Define bounding box for Cologne: [south,west,north,east]
bounding_box = "(50.8700,6.8000,51.0500,7.0500)"

# Overpass QL query for supermarkets in the bounding box
overpass_query = f"""
[out:json];
(
    node["shop"="supermarket"]{bounding_box};
    way["shop"="supermarket"]{bounding_box};
    relation["shop"="supermarket"]{bounding_box};
);
out center;
"""

result = api.query(overpass_query)

In [45]:
print(overpass_query)


[out:json];
(
    node["shop"="supermarket"](50.8700,6.8000,51.0500,7.0500);
    way["shop"="supermarket"](50.8700,6.8000,51.0500,7.0500);
    relation["shop"="supermarket"](50.8700,6.8000,51.0500,7.0500);
);
out center;



In [56]:
result.nodes[0].tags.get("name")
result.ways[0].tags.get("name")
result.relations[0].tags.get("name")

'REWE'

In [82]:
markets = []
for obj in result.nodes + result.ways + result.relations:
	market = {
		"name": obj.tags.get("name"),
		"id": obj.id,
	}
	if isinstance(obj, overpy.Node):
		market["lat"] = obj.lat
		market["lon"] = obj.lon
	elif isinstance(obj, overpy.Way):
		market["lat"] = obj.center_lat
		market["lon"] = obj.center_lon
	elif isinstance(obj, overpy.Relation):
		market["lat"] = obj.center_lat
		market["lon"] = obj.center_lon
	else:
		raise ValueError(f"Unknown type: {type(obj)}")
	markets.append(market)
		
markets = pd.DataFrame(markets)
markets.head(3)

In [95]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
for _, market in markets.iterrows():
	folium.CircleMarker(
		location=(market.lat, market.lon),
		popup=market["name"],
		radius=1,
		color="red",
	).add_to(m)
m


In [96]:
area_of_interest = nodes.geometry.unary_union.convex_hull
markets = gpd.GeoDataFrame(markets, geometry=gpd.points_from_xy(markets.lon, markets.lat))
# only keep markets within area of interest
markets = markets[markets.within(area_of_interest)]
markets

name         id         lat        lon  \
0    Netto Marken-Discount   55441040  50.9408725  7.0081399   
1                 Kaufland  102991868  50.9463208  6.9218135   
2    Netto Marken-Discount  232289350  50.9585924  6.9497996   
3               Netto City  242515981  50.9255261  6.9581475   
4                     REWE  243924635  50.9547763  6.9168738   
..                     ...        ...         ...        ...   
368                   Lidl  798140989  50.9505915  7.0005266   
369            REWE Center  816551392  50.9854625  6.9456900   
370               ALDI Süd  868619074  50.8987225  6.8862791   
371           Edeka Engels  901623455  50.9974473  6.9139239   
373                   Lidl   11026640  50.8934158  6.9033183   

                     geometry  
0    POINT (7.00814 50.94087)  
1    POINT (6.92181 50.94632)  
2    POINT (6.94980 50.95859)  
3    POINT (6.95815 50.92553)  
4    POINT (6.91687 50.95478)  
..                        ...  
368  POINT (7.00053 50.95059)  
369  POINT (6.94569 50.98546)  
370  POINT (6.88628 50.89872)  
371  POINT (6.91392 50.99745)  
373  POINT (6.90332 50.89342)  

[230 rows x 5 columns]

In [106]:
markets = add_nearest_osm_node_id(markets, nodes)
markets["count"] = 1
markets

name         id         lat        lon  \
0    Netto Marken-Discount   55441040  50.9408725  7.0081399   
1                 Kaufland  102991868  50.9463208  6.9218135   
2    Netto Marken-Discount  232289350  50.9585924  6.9497996   
3               Netto City  242515981  50.9255261  6.9581475   
4                     REWE  243924635  50.9547763  6.9168738   
..                     ...        ...         ...        ...   
368                   Lidl  798140989  50.9505915  7.0005266   
369            REWE Center  816551392  50.9854625  6.9456900   
370               ALDI Süd  868619074  50.8987225  6.8862791   
371           Edeka Engels  901623455  50.9974473  6.9139239   
373                   Lidl   11026640  50.8934158  6.9033183   

                     geometry  nearest_osm_node_id   distance  count  
0    POINT (7.00814 50.94087)           2725476496   6.737762      1  
1    POINT (6.92181 50.94632)           1246265182   9.802642      1  
2    POINT (6.94980 50.95859)           1680834812  19.672917      1  
3    POINT (6.95815 50.92553)           3890976981  22.818948      1  
4    POINT (6.91687 50.95478)           6908409244  30.201176      1  
..                        ...                  ...        ...    ...  
368  POINT (7.00053 50.95059)           7464862015  27.213849      1  
369  POINT (6.94569 50.98546)           7626188601  29.966769      1  
370  POINT (6.88628 50.89872)           8096600395  41.214910      1  
371  POINT (6.91392 50.99745)           1684392657  69.915888      1  
373  POINT (6.90332 50.89342)           7435945480  35.178416      1  

[230 rows x 8 columns]

In [118]:
labels = read_labels_for_nodes(mcr5_output_path, markets.nearest_osm_node_id.unique())
labels.head(3)

In [121]:
labels = labels.merge(
    markets[["count", "nearest_osm_node_id"]],
    left_on="target_id_osm",
    right_on="nearest_osm_node_id",
)
labels.head(3)

target_id_osm   time  cost  n_transfers human_readable_time  \
0      506371548  34186     0            0            09:29:46   
1      506371548  31132     0            1            08:38:52   
2      506371548  31132     0            2            08:38:52   

      start_id_hex  count  nearest_osm_node_id  
0  891fa1983dbffff      1            506371548  
1  891fa1983dbffff      1            506371548  
2  891fa1983dbffff      1            506371548

In [122]:
max_transfers = 1
max_time = strtime.str_time_to_seconds("08:15:00")
max_cost = 0

In [123]:
selected_labels = labels[
	(labels["time"] <= max_time)
	& (labels["n_transfers"] <= max_transfers)
	& (labels["cost"] <= max_cost)
]

In [124]:
reachable = selected_labels.groupby("start_id_hex")["count"].sum()

In [125]:
reachable.max()

146

In [129]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(reachable.to_dict(), m)
# for location_mapping in location_mappings:
# 	node = nodes_by_id.loc[location_mapping.osm_node_id]
# 	folium.CircleMarker(
# 		location=(node.lat, node.lon),
# 		icon=folium.Icon(color="green"),
# 		radius=1,
# 		color="red",
# 	).add_to(m)
m